In [33]:
import os
import json
import pandas as pd
import numpy as np
import sys
import copy
from datetime import datetime
sys.path.append('../../Scripts')

from preprocess_daily import DailyPreprocessor
# from generate_signals import SignalGenerator
self = DailyPreprocessor()
# sg = SignalGenerator()

self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.


이동류정보 불러오는 중: 100%|██████████| 17280/17280 [00:12<00:00, 1341.11it/s]


In [34]:
self.make_match6()
self.make_matching()

In [35]:
self.child_ids

['c30', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']

In [36]:
# initialize_state
'''
비보호우회전신호 (g) 배정

input :
(1) net : 네트워크
(2) nodes : 노드 목록
(3) histids : 모든 교차로에 대한 시작유닉스 (시작유닉스, A현시, B현시)별 현시시간, 진입·진출엣지

output : node2init
- 각 노드를 초기화된 신호로 맵핑하는 딕셔너리
- 초기화된 신호란, 우회전을 g로 나머지는 r로 지정한 신호를 말함.
'''
self.nodes = [self.net.getNode(node_id) for node_id in self.node_ids]
self.node2init = {}
# 모든 노드들을 순회
for node in self.nodes:
    node_id = node.getID()
    # 모든 connection
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    # i번째 connection : ci
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        # j번째 connection : cj
        # 합류지점이 다르면서 상충되는 cj가 존재하면 are_foes = True (r)
        # 그외의 경우에는 are_foes = False (g)
        for j, cj in conns:
            # ci, cj의 합류지점이 같으면 통과
            if ci.getTo() == cj.getTo():
                continue
            # ci, cj가 상충되면 are_foes를 True로 지정.
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    self.node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                self.node2init[node_id][index] = 'r'

In [37]:
''.join(self.node2init['i2'])

'rrgrrrr'

In [38]:
old_match6 = self.match6
old_matching = self.matching

In [39]:
# assign_signals
self.match6 = old_match6.copy()
self.matching = old_matching.copy()

# assign signals on matching
self.matching['init_state'] = self.matching['node_id'].map(self.node2init)
self.matching['state'] = self.matching['init_state'].map(lambda x:''.join(x))
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'state']]

# assign signals on match6

self.match6 = self.match6.reset_index(drop=True)
self.match6['init_state'] = self.match6['node_id'].map(self.node2init)
self.match6['state'] = self.match6['init_state'].map(lambda x:''.join(x))

# match6의 각 행을 순회
for i, row in self.match6.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = row.inc_edge
    out_edge = row.out_edge
    state = copy.deepcopy(self.node2init)[node_id]
    if (pd.isna(inc_edge)) or (pd.isna(out_edge)):
        continue
    if (move_no != 21):
        # print(i, node_id, move_no, ''.join(state))
        inc_edge = self.net.getEdge(inc_edge)
        out_edge = self.net.getEdge(out_edge)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
            # print(i, node_id, move_no, index, ''.join(state))
        self.match6.at[i, 'state'] = ''.join(state)

self.match6 = self.match6.dropna(subset='state')
self.match6 = self.match6.reset_index(drop=True)
self.match6 = self.match6[['inter_no', 'node_id', 'phase_no', 'ring_type', 'move_no', 'state']]

In [40]:
self.matching

inter_no node_id  move_no              state
0        175      i0        1  grrrgrrGgrrrrrgrr
1        175      i0        2  grrrgrrrgrrrrrgGr
2        175      i0        3  grrrgrrrgrrrrGgrr
3        175      i0        4  gGGrgrrrgrrrrrgrr
4        175      i0        5  grrrgrrrgrrrrrgrG
..       ...     ...      ...                ...
70       210      i6       21   grrrgrrrrgrrgrrr
71       210      i6       21   grrrgrrrrgrrgrrr
72       210      i6       21   grrrgrrrrgrrgrrr
73       210      i6       21   grrrgrrrrgrrgrrr
74       210     u60       19          ggggggggG

[75 rows x 4 columns]

In [41]:
self.match6.to_csv('match6.csv',index=False)
self.matching.to_csv('matching.csv',index=False)
with open('node2init.json', 'w') as file:
    json.dump(self.node2init, file)

In [42]:
import numpy as np
import json
from generate_signals import SignalGenerator
self = SignalGenerator()
self.prepare_data() # 1
self.process_history() # 2
self.process_movement() # 3

self.match6 = pd.read_csv('match6.csv')
self.matching = pd.read_csv('matching.csv')
with open('node2init.json', 'r') as file:
    self.node2init = json.load(file)


1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
2. 신호이력 테이블을 변환합니다.
3. 이동류정보 테이블을 변환합니다.


In [43]:
self.matching

inter_no node_id  move_no              state
0        175      i0        1  grrrgrrGgrrrrrgrr
1        175      i0        2  grrrgrrrgrrrrrgGr
2        175      i0        3  grrrgrrrgrrrrGgrr
3        175      i0        4  gGGrgrrrgrrrrrgrr
4        175      i0        5  grrrgrrrgrrrrrgrG
..       ...     ...      ...                ...
70       210      i6       21   grrrgrrrrgrrgrrr
71       210      i6       21   grrrgrrrrgrrgrrr
72       210      i6       21   grrrgrrrrgrrgrrr
73       210      i6       21   grrrgrrrrgrrgrrr
74       210     u60       19          ggggggggG

[75 rows x 4 columns]

In [44]:
# movedur : movements and durations
self.movedur = pd.merge(self.hrhists, self.movement_updated, how='inner', on=['inter_no', 'start_unix', 'phas_A', 'phas_B'])
self.movedur = self.movedur[['inter_no', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration']]
display(self.movedur.head())

inter_no  start_unix  phas_A  phas_B  move_A  move_B  duration
0       175  1704416178       1       1       8       4        54
1       175  1704416178       2       2       7       3        57
2       175  1704416178       3       3       6       1        42
3       175  1704416178       3       4       6       2        28
4       175  1704416178       4       4       5       2        47

In [45]:
# histid
self.histid = self.movedur.copy()
self.histid['node_id'] = self.histid['inter_no'].map(self.inter2node)
histid_start = self.present_time - 600
self.histid = self.histid[self.histid.start_unix > histid_start]

mapping_dict = self.matching.set_index(['node_id', 'move_no'])['state'].to_dict()

for i, row in self.histid.iterrows():
    node_id = row.node_id
    move_A = row.move_A
    move_B = row.move_B

    # A링의 state 지정
    if (node_id, move_A) in mapping_dict:
        state_A = mapping_dict[(node_id, move_A)]
    else:
        state_A = ''.join(self.node2init[node_id])
    # self.histid.at[i, 'state_A'] = state_A

    # B링의 state 지정
    if (node_id, move_B) in mapping_dict:
        state_B = mapping_dict[(node_id, move_B)]
    else:
        state_B = ''.join(self.node2init[node_id])
    # self.histid.at[i, 'state_B'] = state_B

    # 통합된 state 지정
    state = ''
    for a, b in zip(state_A,state_B):
        if a == b:
            state += a
        elif (a == 'G') or (b == 'G'):
            state += 'G'
    self.histid.at[i, 'state'] = state
display(self.histid)

inter_no  start_unix  phas_A  phas_B  move_A  move_B  duration node_id  \
10        175  1704416540       1       1       8       4        43      i0   
11        175  1704416540       2       2       7       3        46      i0   
12        175  1704416540       3       3       6       1        33      i0   
13        175  1704416540       3       4       6       2        23      i0   
14        175  1704416540       4       4       5       2        37      i0   
..        ...         ...     ...     ...     ...     ...       ...     ...   
255       201  1704417410       1       1       8       3        33      i8   
256       201  1704417410       2       2       5       2        36      i8   
257       201  1704417410       3       3       6       2        25      i8   
258       201  1704417410       4       4       6       1        58      i8   
259       201  1704417410       5       5       7       4        18      i8   

                 state  
10   gGGrgrrrgGGGGrgrr  
11   grrGgrrrgrrrrGgrr  
12   grrrgGGGgrrrrrgrr  
13   grrrgGGrgrrrrrgGr  
14   grrrgrrrgrrrrrgGG  
..                 ...  
255   grrrrrrrgGGGgrrr  
256   grrrrrrrgrrrgGGG  
257   grrrGGGrgrrrgGGr  
258   grrrGGGGgrrrgrrr  
259   gGGGrrrrgrrrgrrr  

[203 rows x 9 columns]

In [46]:
new_histids = []
for parent_id in self.parent_ids:
    for child_id in self.pa2ch[parent_id]:
        new_histid = self.histid.copy()[self.histid.node_id==parent_id].drop(columns='state')
        # new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = self.match6[self.match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]

            # A링의 state 지정
            state_A = Arow.iloc[0].state
            # new_histid.at[i, 'state_A'] = state_A

            # B링의 state 지정
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            state_B = Brow.iloc[0].state
            # new_histid.at[i, 'state_B'] = state_B

            # 통합된 state 지정
            state = ''
            for a, b in zip(state_A,state_B):
                if a == b:
                    state += a
                elif (a == 'G') or (b == 'G'):
                    state += 'G'
            new_histid.at[i, 'state'] = state
            new_histid.at[i, 'node_id'] = child_id
        new_histids.append(new_histid)
new_histids = pd.concat(new_histids)
self.histids = pd.concat([self.histid.copy(), new_histids])
self.histids = self.histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
self.histids = self.histids[['inter_no', 'node_id', 'start_unix', 'phas_A', 'phas_B', 'move_A', 'move_B', 'duration', 'state']]
self.histids

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0         202      i9  1704416410       1       1       6       2        46   
1         202      i9  1704416410       2       2      17      18       114   
2         210      i6  1704416420       1       1       6      18        28   
3         210      i6  1704416420       1       2       6       2        15   
4         210      i6  1704416420       2       2       5       2        43   
..        ...     ...         ...     ...     ...     ...     ...       ...   
383       210     u60  1704417420       1       1       6      18        16   
384       210     u60  1704417420       1       2       6       2         8   
385       210     u60  1704417420       2       2       5       2        24   
386       210     u60  1704417420       3       3       7       4        39   
387       210     u60  1704417420       4       4       8       3        13   

                state  
0                GGGG  
1                rrrr  
2    grrrgGGGrgrrgrrr  
3    grrrgGGGrgrrgGGr  
4    grrrgrrrrgrrgGGG  
..                ...  
383         ggggggggr  
384         ggggggggr  
385         ggggggggG  
386         ggggggggr  
387         ggggggggr  

[388 rows x 9 columns]

In [48]:
self.histids[:60]

inter_no node_id  start_unix  phas_A  phas_B  move_A  move_B  duration  \
0        202      i9  1704416410       1       1       6       2        46   
1        202      i9  1704416410       2       2      17      18       114   
2        210      i6  1704416420       1       1       6      18        28   
3        210      i6  1704416420       1       2       6       2        15   
4        210      i6  1704416420       2       2       5       2        43   
5        210      i6  1704416420       3       3       7       4        70   
6        210      i6  1704416420       4       4       8       3        24   
7        210     u60  1704416420       1       1       6      18        28   
8        210     u60  1704416420       1       2       6       2        15   
9        210     u60  1704416420       2       2       5       2        43   
10       210     u60  1704416420       3       3       7       4        70   
11       210     u60  1704416420       4       4       8       3        24   
12       206      i7  1704416459       1       1       8       4        45   
13       206      i7  1704416459       2       2      17      18        53   
14       206      i7  1704416459       3       3       8       4        26   
15       206      i7  1704416459       4       4      17      18        26   
16       178     c30  1704416520       1       1       8       4        38   
17       178     c30  1704416520       2       2       7       3        39   
18       178     c30  1704416520       3       3       5       2        43   
19       178     c30  1704416520       4       4       6       1        22   
20       177      i2  1704416520       1       1       8       4        43   
21       177      i2  1704416520       2       2       7       3        27   
22       177      i2  1704416520       3       3      17      18        70   
23       177      i2  1704416520       4       4       5       1        40   
24       178      i3  1704416520       1       1       8       4        38   
25       178      i3  1704416520       2       2       7       3        39   
26       178      i3  1704416520       3       3       5       2        43   
27       178      i3  1704416520       4       4       6       1        22   
28       177     u20  1704416520       1       1       8       4        43   
29       177     u20  1704416520       2       2       7       3        27   
30       177     u20  1704416520       3       3      17      18        70   
31       177     u20  1704416520       4       4       5       1        40   
32       178     u30  1704416520       1       1       8       4        38   
33       178     u30  1704416520       2       2       7       3        39   
34       178     u30  1704416520       3       3       5       2        43   
35       178     u30  1704416520       4       4       6       1        22   
36       178     u31  1704416520       1       1       8       4        38   
37       178     u31  1704416520       2       2       7       3        39   
38       178     u31  1704416520       3       3       5       2        43   
39       178     u31  1704416520       4       4       6       1        22   
40       178     u32  1704416520       1       1       8       4        38   
41       178     u32  1704416520       2       2       7       3        39   
42       178     u32  1704416520       3       3       5       2        43   
43       178     u32  1704416520       4       4       6       1        22   
44       175      i0  1704416540       1       1       8       4        43   
45       175      i0  1704416540       2       2       7       3        46   
46       175      i0  1704416540       3       3       6       1        33   
47       175      i0  1704416540       3       4       6       2        23   
48       175      i0  1704416540       4       4       5       2        37   
49       176      i1  1704416540       1       1       8       4        37   
50       176      i1  1704